In [70]:
import pandas as pd
import openpyxl
import os
from tqdm import tqdm
from datetime import datetime

In [71]:
DB_FILE = 'files/source.xlsx'
TEMPLATE_FILE = 'files/template.xlsx'
OUTPUT_FOLDER = 'files/output/'


MAPPING = {
    'Дата МО' : 'Q1',
    'Время МО' : 'Q2',
    'Номер направления': 'A13',
    'Фамилия, имя, отчество': 'D21',
    'Дата рождения': 'D22',
    'Структурное подразделение': 'F26',
    'Должность работника ': 'F27',
    '''Наименование вредных производственных факторов или фидов работ (приложение к приказу Минздрава РФ от 28.01.2021 №29Н)''': 'F30'
}

if not os.path.exists(OUTPUT_FOLDER):
    os.makedirs(OUTPUT_FOLDER)

In [72]:
df = pd.read_excel(DB_FILE)
print(f"Всего сотрудников в списке: {len(df)}")
# print(df.columns.tolist())

df.columns

Всего сотрудников в списке: 1482


Index(['Дата МО', 'Время МО', 'Номер направления', 'Фамилия, имя, отчество',
       'Должность работника ', 'Дата рождения', 'Структурное подразделение',
       'Наименование вредных производственных факторов или фидов работ (приложение к приказу Минздрава РФ от 28.01.2021 №29Н)',
       'Примечания'],
      dtype='object')

In [73]:
df.head()

Дата МО Время МО  Номер направления         Фамилия, имя, отчество  \
0 2026-02-02    09:30                  1       Орлова Ксения Николаевна   
1 2026-02-02    09:35                  2  Камнев Владимир Александрович   
2 2026-02-02    09:40                  3       Стогов Юрий Владимирович   
3 2026-02-02    09:45                  4      Алферов Владимир Петрович   
4 2026-02-02    09:50                  5   Савостиков Сергей Алексеевич   

                                Должность работника  Дата рождения  \
0                                             Доцент    17.07.1985   
1  Специалист по учебно-методической работе 1 кат...    24.01.1955   
2                                             Доцент    05.01.1959   
3  Заместитель главного инженера исследовательско...    08.11.1948   
4  Слесарь по ремонту и обслуживанию систем венти...    20.05.1988   

                           Структурное подразделение  \
0  кафедра радиационной физики и безопасности ато...   
1  кафедра радиационной физики и безопасности ато...   
2  кафедра теоретической и экспериментальной физи...   
3  исследовательский реактор типовой атомного центра   
4  теплоэнергетический отдел службы главного инже...   

  Наименование вредных производственных факторов или фидов работ (приложение к приказу Минздрава РФ от 28.01.2021 №29Н)  \
0                                                4.1                                                                      
1                                                4.1                                                                      
2                                                4.1                                                                      
3                                                4.1                                                                      
4                                           5.1, 6.2                                                                      

   Примечания  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN

In [74]:
for index, row in tqdm(df.iterrows(), total=len(df)):
    wb = openpyxl.load_workbook(TEMPLATE_FILE)
    ws = wb.active

    # Заполняем поля по словарю MAPPING
    for excel_col, cell_address in MAPPING.items():
        value = row.get(excel_col, "")

        if pd.isna(value):
            value = ""

        if cell_address == 'A13':
            ws[cell_address] = f"НАПРАВЛЕНИЕ № {value}"

        elif isinstance(value, (datetime, pd.Timestamp)):
            ws[cell_address] = value.strftime('%d.%m.%Y')

        else:
            ws[cell_address] = str(value)

    num = str(row.get('Номер направления', index + 1))
    fio = str(row.get('Фамилия, имя, отчество')).strip().replace(' ', '_')
    file_name = f"Направление_№{num}_{fio}.xlsx"

    save_path = os.path.join(OUTPUT_FOLDER, file_name)
    wb.save(save_path)

print(f"\nФайлы сохранены в '{OUTPUT_FOLDER}'")

100%|██████████| 1482/1482 [00:54<00:00, 27.41it/s]


Файлы сохранены в 'files/output/'
